In [2]:
import numpy as np
import pandas as pd



In [3]:
with open("../christie/Death on the Nile.txt", encoding='utf8') as f:
    file= f.read()
   

In [4]:
raw= file.split("CHAPTER")[1:]

In [5]:

# Create the dataframe
raw = pd.DataFrame({"chapter": raw})
raw.head()


chapter
0   1\n\n\n\n\n\nLinnet Ridgeway!\n\n\n\n\n\n"Tha...
1   1\n\n\n\n\n\n''That's Hercule Poirot, the det...
2   2\n\n\n\n\n\nDinner was over.\n\n\n\n\n\nThe ...
3   3\n\n\n\n\n\n"M. Poirot."\n\n\n\n\n\nPoirot g...
4   4\n\n\n\n\n\nHercule Poirot found Jacqueline ...

In [6]:
chapters = raw.copy()
chapters['chapter_number'] = chapters.chapter.str.split("\n").str[0]
#chapters['chapter_num'] = chapters.chapter_title.str.split(" ").str[0]
#chapters['title'] = chapters.chapter_title.str.split(" ").str[1]

chapters.head()

chapter chapter_number
0   1\n\n\n\n\n\nLinnet Ridgeway!\n\n\n\n\n\n"Tha...              1
1   1\n\n\n\n\n\n''That's Hercule Poirot, the det...              1
2   2\n\n\n\n\n\nDinner was over.\n\n\n\n\n\nThe ...              2
3   3\n\n\n\n\n\n"M. Poirot."\n\n\n\n\n\nPoirot g...              3
4   4\n\n\n\n\n\nHercule Poirot found Jacqueline ...              4

In [7]:
def remove_chapter_title(text):
    length = len(text.split("\n")[0]) + 2
    return text[length:]

In [8]:

chapters['chapter'] = chapters.chapter.map(remove_chapter_title)
#chapters.drop('chapter_number', inplace=True, axis=1)
chapters.head()


chapter chapter_number
0  \n\n\n\nLinnet Ridgeway!\n\n\n\n\n\n"That's He...              1
1  \n\n\n\n''That's Hercule Poirot, the detective...              1
2  \n\n\n\nDinner was over.\n\n\n\n\n\nThe terrac...              2
3  \n\n\n\n"M. Poirot."\n\n\n\n\n\nPoirot got has...              3
4  \n\n\n\nHercule Poirot found Jacqueline de Bel...              4

In [9]:
def unnest_tokens(dataframe, column, tokenizer, new_column='word'): 
    """
    Applies a tokenizer to a column and then unnest the dataframe
    
    dataframe: dataframe with text
    column: name of the column with the text
    new_column: what you want the column of words to be called
    tokenizer: a function to be used to tokenize the text
    """ 
    new_column_num = new_column + "_num"
    df = ( dataframe[column]
              .apply(tokenizer)
              .apply(pd.Series)
              .stack()
              .reset_index(level=1)
              .rename(columns={0: new_column, "level_1":new_column_num})
              .join(dataframe.drop(column, axis=1), how='left')
              .reset_index(drop=True)
         )
    df[new_column_num] = pd.to_numeric(df[new_column_num])
    df[new_column_num] = df[new_column_num] + 1
    return df


In [10]:
def paragraph_tokenizer(text):
    return text.split("\n\n\n\n\n\n")


In [11]:
paragraphs = unnest_tokens(chapters, "chapter", paragraph_tokenizer, "paragraph")
paragraphs.head()

paragraph_num                                          paragraph  \
0              1                           \n\n\n\nLinnet Ridgeway!   
1              2  "That's Her." said Mr. Burnaby, the landlord o...   
2              3                           He nudged his companion.   
3              4  The two men stared with round bucolic eyes and...   
4              5  A big scarlet Rolls-Royce had just stopped in ...   

  chapter_number  
0              1  
1              1  
2              1  
3              1  
4              1

In [12]:
paragraphs.paragraph[5]

'A girl jumped out, a girl without a hat and wearing a frock that looked (but only looked) simple. A girl with golden hair and straight autocratic features--a girl with a lovely shape--a girl such as was seldom seen in MaltonunderWode.'

In [13]:
paragraphs['paragraph'] = paragraphs.paragraph.str.replace("\n", " ")

In [14]:
import spacy
nlp = spacy.load('en')


In [15]:
def sentence_tokenizer(text):
    doc = nlp(text)
    sentences = [sent.string.strip() for sent in doc.sents]
    return sentences

In [16]:
sentences = unnest_tokens(paragraphs, "paragraph", sentence_tokenizer, "sentence")

In [17]:
sentences.head()

sentence_num                                           sentence  \
0             1                                   Linnet Ridgeway!   
1             1  "That's Her." said Mr. Burnaby, the landlord o...   
2             1                           He nudged his companion.   
3             1  The two men stared with round bucolic eyes and...   
4             1  A big scarlet Rolls-Royce had just stopped in ...   

   paragraph_num chapter_number  
0              1              1  
1              2              1  
2              3              1  
3              4              1  
4              5              1

In [18]:

def word_tokenizer(text):
    doc = nlp(text)
    words = [[token.text, token.lemma_, token.pos_, token.is_stop] for token in doc]
    return words

In [19]:
words = unnest_tokens(sentences, "sentence", word_tokenizer, "word")

In [20]:
words.head()

word_num                                word  sentence_num  paragraph_num  \
0         1      [Linnet, linnet, PROPN, False]             1              1   
1         2  [Ridgeway, ridgeway, PROPN, False]             1              1   
2         3                [!, !, PUNCT, False]             1              1   
3         1                [", ", PUNCT, False]             1              2   
4         2            [That, that, DET, False]             1              2   

  chapter_number  
0              1  
1              1  
2              1  
3              1  
4              1

In [21]:
words[['word', 'lemma', 'POS', "stop"]] = pd.DataFrame(words.word.values.tolist())

In [22]:
words.head()

word_num      word  sentence_num  paragraph_num chapter_number     lemma  \
0         1    Linnet             1              1              1    linnet   
1         2  Ridgeway             1              1              1  ridgeway   
2         3         !             1              1              1         !   
3         1         "             1              2              1         "   
4         2      That             1              2              1      that   

     POS   stop  
0  PROPN  False  
1  PROPN  False  
2  PUNCT  False  
3  PUNCT  False  
4    DET  False

In [27]:
from vega3 import VegaLite
from vega3 import Vega

In [29]:
df = words[['chapter_number', 'paragraph_num', 'sentence_num', 'word_num']]
df.head()

chapter_number  paragraph_num  sentence_num  word_num
0              1              1             1         1
1              1              1             1         2
2              1              1             1         3
3              1              2             1         1
4              1              2             1         2

In [30]:
VegaLite({
  "width": 400,
  "mark": "bar",
  "encoding": {
    "y": {"type": "quantitative","field": "chapter_num", "aggregate": "count"},
    "x": {"type": "quantitative","field": "chapter_num"},
    "size": {"value": 30}
  }
}, df)

In [31]:
len(words.lemma.unique())

5606

In [32]:
words.POS.unique()

array(['PROPN', 'PUNCT', 'DET', 'VERB', 'PRON', 'NOUN', 'ADP', 'ADJ',
       'NUM', 'CCONJ', 'ADV', 'PART', 'INTJ', 'X', 'SYM', 'SPACE'],
      dtype=object)

In [33]:
names = words.query("POS == 'DET'")

In [34]:

names.lemma.unique()

array(['that', 'the', 'a', 'all', 'no', 'another', 'those', 'an', 'any',
       'these', 'some', 'every', 'this', 'la', 'each', 'both', 'either',
       'sheshe', 'neither', 'half', '--that', 'th', "they're", 'au'],
      dtype=object)

In [35]:

words.index[words.stop == True]

Int64Index([    13,     15,     16,     22,     26,     29,     33,     44,
                45,     47,
            ...
            101337, 101339, 101342, 101343, 101344, 101345, 101347, 101349,
            101350, 101356],
           dtype='int64', length=37037)

In [36]:
wordlist = (words
            .query("stop == False")
            .query("POS != 'PUNCT'")
)

In [38]:
w = wordlist.groupby("word").count()
w.head()

word_num  sentence_num  paragraph_num  chapter_number  lemma  POS  stop
word                                                                         
             1             1              1               1      1    1     1
$            1             1              1               1      1    1     1
&            1             1              1               1      1    1     1
'           11            11             11              11     11   11    11
'd         121           121            121             121    121  121   121